# Домашнее задание  № 5. Матричные разложения/Тематическое моделирование

### Задание № 1 (4 балла)

Попробуйте матричные разложения с 4 классификаторами - SGDClassifier, KNeighborsClassifier,  RandomForest, ExtraTreesClassifier (про него подробнее почитайте в документации, он похож на RF). Используйте и NMF, и SVD. Сравните результаты на кросс-валидации и выберите лучшее сочетание.

В итоге у вас должно получиться, как минимум 8 моделей (два разложения на каждый классификатор). Используйте 1 и те же параметры кросс-валидации. Параметры векторизации, параметры K в матричных разложениях, параметры классификаторов могут быть разными между экспериментами.

Можете взять поменьше данных, если все будет обучаться слишком долго (не ставьте параметр K слишком большим в NMF, иначе точно будет слишком долго)

In [ ]:
!pip install gensim pymorphy2 seaborn pyLDAvis

In [ ]:
import gensim
import pandas as pd
import numpy as np
from pymorphy2 import MorphAnalyzer
morph = MorphAnalyzer()
import pyLDAvis.gensim_models
from collections import Counter
from string import punctuation
from razdel import tokenize as razdel_tokenize
from sklearn.decomposition import TruncatedSVD, NMF, PCA, LatentDirichletAllocation
from sklearn.manifold import TSNE
from sklearn.feature_extraction.text import TfidfVectorizer, CountVectorizer, TfidfTransformer
from sklearn.metrics.pairwise import cosine_distances
from sklearn.ensemble import RandomForestClassifier
from sklearn.linear_model import SGDClassifier
from sklearn.neighbors import KNeighborsClassifier
from sklearn.ensemble import ExtraTreesClassifier
from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score, confusion_matrix
from sklearn.pipeline import Pipeline
from sklearn.model_selection import KFold, StratifiedKFold
from matplotlib import pyplot as plt
import seaborn as sns

In [ ]:
avito_df = pd.read_csv('avito_category_classification.csv')
avito_df.head(5)

In [ ]:
%%time
def lemmatization(tokens):
    lemmas = []
    for token in tokens:
        token_parsed = morph.parse(token)
        lemmas.append(token_parsed[0].normal_form)
    return(lemmas)

def strip_punct(lemmas):
    clean_lemmas = [lem.strip(punctuation) for lem in lemmas]
    result = ' '.join(clean_lemmas)
    return result

avito_df['description_norm'] = avito_df['description'].apply(lambda x: x.lower().split())

avito_df['description_norm'] = avito_df['description_norm'].apply(lemmatization)

avito_df['description_norm'] = avito_df['description_norm'].apply(strip_punct)

avito_df.head(5)

In [ ]:
def eval_table(X, y, pipeline, N=6):
    # зафиксируем порядок классов
    labels = list(set(y))
    
    # метрики отдельных фолдов будет хранить в табличке
    fold_metrics = pd.DataFrame(index=labels)
    # дополнительно также соберем таблицу ошибок
    errors = np.zeros((len(labels), len(labels)))
    
    # создаем стратегию кросс-валидации
    # shuffle=True (перемешивание) - часто критично важно указать
    # т.к. данные могут быть упорядочены и модель на этом обучится
    kfold = StratifiedKFold(n_splits=N, shuffle=True, )
        
    for i, (train_index, test_index) in enumerate(kfold.split(X, y)):
        # fit-predict как и раньше, но сразу пайплайном
        pipeline.fit(X[train_index], y[train_index])
        preds = pipeline.predict(X[test_index])
        
        # записываем метрику и индекс фолда
        fold_metrics[f'precision_{i}'] = precision_score(y[test_index], preds, labels=labels, average=None)
        fold_metrics[f'recall_{i}'] = recall_score(y[test_index], preds, labels=labels, average=None)
        fold_metrics[f'f1_{i}'] = f1_score(y[test_index], preds, labels=labels, average=None)
        
        # пришлось убрать normalize='true'
        # TypeError: sklearn.metrics. confusion_matrix() got an unexpected keyword argument 'normalize'
        errors += confusion_matrix(y[test_index], preds, labels=labels)
    
    # таблица для усредненных значений
    # тут мы берем колонки со значениями и усредняем их
    # часто также все метрики сразу суммируют и в конце просто делят на количество фолдов
    # но мы тут помимо среднего также хотим посмотреть на стандартное отклонение
    # чтобы понять как сильно варьируются оценки моделей
    result = pd.DataFrame(index=labels)
    result['precision'] = fold_metrics[[f'precision_{i}' for i in range(N)]].mean(axis=1).round(2)
    result['precision_std'] = fold_metrics[[f'precision_{i}' for i in range(N)]].std(axis=1).round(2)
    
    result['recall'] = fold_metrics[[f'recall_{i}' for i in range(N)]].mean(axis=1).round(2)
    result['recall_std'] = fold_metrics[[f'recall_{i}' for i in range(N)]].std(axis=1).round(2)
    
    result['f1'] = fold_metrics[[f'f1_{i}' for i in range(N)]].mean(axis=1).round(2)
    result['f1_std'] = fold_metrics[[f'f1_{i}' for i in range(N)]].std(axis=1).round(2)
    
    # добавим одну колонку со средним по всем классам
    result.loc['mean'] = result.mean().round(2)
    # проценты ошибок просто усредняем
    errors /= N
    
    return result, errors

### 1.1. SGDClassifier - NMF

In [ ]:
SDG_NMF = Pipeline([
    ('bow', CountVectorizer(tokenizer=lambda x: x.split(), ngram_range=(1,2), min_df=6, max_df=0.5)),
    ('tfidf', TfidfTransformer()),
    ('decomposition', NMF(100)),
    ('clf', SGDClassifier(max_iter=1000, tol=1e-3))
])

In [ ]:
%%time
metrics_SDG_NMF, errors_SDG_NMF = eval_table(avito_df['description_norm'], avito_df['category_name'],
                                                   SDG_NMF)

In [ ]:
metrics_SDG_NMF

In [ ]:
plt.figure(figsize=(6, 6))
sns.heatmap(errors_SDG_NMF, xticklabels=metrics_SDG_NMF.index.tolist()[:-1], 
            yticklabels=metrics_SDG_NMF.index.tolist()[:-1])
plt.title('SGDClassifier - NMF')
plt.show()

### 1.2. SGDClassifier - SVD

In [ ]:
SDG_SVD = Pipeline([
    ('bow', CountVectorizer(tokenizer=lambda x: x.split(), ngram_range=(1,2), min_df=6, max_df=0.5)),
    ('svd', TruncatedSVD(500)),
    ('clf', SGDClassifier(max_iter=1000, tol=1e-3))
])

In [ ]:
%%time
metrics_SDG_SVD, errors_SDG_SVD = eval_table(avito_df['description_norm'], avito_df['category_name'],
                                                   SDG_SVD)

In [ ]:
metrics_SDG_SVD

In [ ]:
plt.figure(figsize=(6, 6))
sns.heatmap(errors_SDG_SVD, xticklabels=metrics_SDG_SVD.index.tolist()[:-1], 
            yticklabels=metrics_SDG_SVD.index.tolist()[:-1])
plt.title('SGDClassifier - SVD')
plt.show()

### 2.1. KNeighborsClassifier - NMF

In [ ]:
KN_NMF = Pipeline([
    ('bow', CountVectorizer(tokenizer=lambda x: x.split(), ngram_range=(1,2), min_df=6, max_df=0.5)),
    ('tfidf', TfidfTransformer()),
    ('decomposition', NMF(100)),
    ('clf', KNeighborsClassifier(n_neighbors=3))
])

In [ ]:
%%time
metrics_KN_NMF, errors_KN_NMF = eval_table(avito_df['description_norm'], avito_df['category_name'],
                                                   KN_NMF)

In [ ]:
metrics_KN_NMF

In [ ]:
plt.figure(figsize=(6, 6))
sns.heatmap(errors_KN_NMF, xticklabels=metrics_KN_NMF.index.tolist()[:-1], 
            yticklabels=metrics_KN_NMF.index.tolist()[:-1])
plt.title('KNeighborsClassifier - NMF')
plt.show()

### 2.2. KNeighborsClassifier - SVD 

In [ ]:
KN_SVD = Pipeline([
    ('bow', CountVectorizer(tokenizer=lambda x: x.split(), ngram_range=(1,2), min_df=6, max_df=0.5)),
    ('svd', TruncatedSVD(500)),
    ('clf', KNeighborsClassifier(n_neighbors=3))
])

In [ ]:
%%time
metrics_KN_SVD, errors_KN_SVD = eval_table(avito_df['description_norm'], avito_df['category_name'],
                                                   KN_SVD)

In [ ]:
metrics_KN_SVD

In [ ]:
plt.figure(figsize=(6, 6))
sns.heatmap(errors_KN_SVD, xticklabels=metrics_KN_SVD.index.tolist()[:-1], 
            yticklabels=metrics_KN_SVD.index.tolist()[:-1])
plt.title('KNeighborsClassifier - SVD')
plt.show()

### 3.1. RandomForest - NMF

In [ ]:
RF_NMF = Pipeline([
    ('bow', CountVectorizer(tokenizer=lambda x: x.split(), ngram_range=(1,2), min_df=6, max_df=0.5)),
    ('tfidf', TfidfTransformer()),
    ('decomposition', NMF(100)),
    ('clf', RandomForestClassifier(max_depth=2, random_state=0))
])

In [ ]:
%%time
metrics_RF_NMF, errors_RF_NMF = eval_table(avito_df['description_norm'], avito_df['category_name'],
                                                   RF_NMF)

In [ ]:
metrics_RF_NMF

In [ ]:
plt.figure(figsize=(6, 6))
sns.heatmap(errors_RF_NMF, xticklabels=metrics_RF_NMF.index.tolist()[:-1], 
            yticklabels=metrics_RF_NMF.index.tolist()[:-1])
plt.title('RandomForest - NMF')
plt.show()

### 3.2. RandomForest - SVD

In [ ]:
RF_SVD = Pipeline([
    ('bow', CountVectorizer(tokenizer=lambda x: x.split(), ngram_range=(1,2), min_df=6, max_df=0.5)),
    ('svd', TruncatedSVD(500)),
    ('clf', RandomForestClassifier(max_depth=2, random_state=0))
])

In [ ]:
%%time
metrics_RF_SVD, errors_RF_SVD = eval_table(avito_df['description_norm'], avito_df['category_name'],
                                                   RF_SVD)

In [ ]:
metrics_RF_SVD

In [ ]:
plt.figure(figsize=(6, 6))
sns.heatmap(errors_RF_SVD, xticklabels=metrics_RF_SVD.index.tolist()[:-1], 
            yticklabels=metrics_RF_SVD.index.tolist()[:-1])
plt.title('RandomForest - SVD')
plt.show()

### 4.1. ExtraTreesClassifier - NMF

In [ ]:
ET_NMF = Pipeline([
    ('bow', CountVectorizer(tokenizer=lambda x: x.split(), ngram_range=(1,2), min_df=6, max_df=0.5)),
    ('tfidf', TfidfTransformer()),
    ('decomposition', NMF(100)),
    ('clf', ExtraTreesClassifier(n_estimators=100, random_state=0))
])

In [ ]:
%%time
metrics_ET_NMF, errors_ET_NMF = eval_table(avito_df['description_norm'], avito_df['category_name'],
                                                   ET_NMF)

In [ ]:
metrics_ET_NMF

In [ ]:
plt.figure(figsize=(6, 6))
sns.heatmap(errors_ET_NMF, xticklabels=metrics_ET_NMF.index.tolist()[:-1], 
            yticklabels=metrics_ET_NMF.index.tolist()[:-1])
plt.title('ExtraTreesClassifier - NMF')
plt.show()

### 4.2. ExtraTreesClassifier - SVD

In [ ]:
ET_SVD = Pipeline([
    ('bow', CountVectorizer(tokenizer=lambda x: x.split(), ngram_range=(1,2), min_df=6, max_df=0.5)),
    ('svd', TruncatedSVD(500)),
    ('clf', ExtraTreesClassifier(n_estimators=100, random_state=0))
])

In [ ]:
%%time
metrics_ET_SVD, errors_ET_SVD = eval_table(avito_df['description_norm'], avito_df['category_name'],
                                                   ET_SVD)

In [ ]:
metrics_ET_SVD

In [ ]:
plt.figure(figsize=(6, 6))
sns.heatmap(errors_ET_SVD, xticklabels=metrics_ET_SVD.index.tolist()[:-1], 
            yticklabels=metrics_ET_SVD.index.tolist()[:-1])
plt.title('ExtraTreesClassifier - SVD')
plt.show()

Выводы:

Лучше всех показали себя SGDClassifier + SVD (средняя точность 0.72, среднее f1 - 0.7) и ExtraTreesClassifier + NMF (средняя точность 0.71, среднее f1 - 0.66);

Хуже всех оказался RandomForestClassifier + SVD (средняя точность 0.16, среднее f1 - 0.11);

Быстрее всех работал RandomForestClassifier + SVD (37.3 s; поспешишь - людей насмешишь);

Дольше всех работал KNeighbours + NMF (4min 31s).

### Задание № 2 (6 баллов)

В Gensim тоже можно добавить нграммы и tfidf. Постройте 1 модель без них (как в семинаре) и еще 3 модели (1 с нграммами, 1 с tfidf и 1 с нграммами и с tfidf). Сравните качество с помощью метрик (перплексия, когерентность) и на глаз. Определите лучшую модель. Для каждой модели выберите 1 самую красивую на ваш взгляд тему.

Используйте данные википедии из семинара. Можете взять поменьше данных, если все обучается долго.

Важное требование - получившиеся модели не должны быть совсем плохими. Если хороших тем не получается, попробуйте настроить гиперпараметры, отфильтровать словарь по-другому. 

Нграммы добавляются вот так (перед созданием словаря)

In [ ]:
texts = [text.split() for text in texts]
ph = gensim.models.Phrases(texts, scoring='npmi', threshold=0.5) # threshold можно подбирать
p = gensim.models.phrases.Phraser(ph)
ngrammed_texts = p[texts] 

# ! не забудьте, что далее вам нужно будет использовать ngrammed_texts

!! В модели с нграммами вначале посмотрите, что получается после преобразования
Если вы выведите несколько первых текстов в ngrammed_texts, то там должно быть что-то такое:

In [ ]:
[text for text in ngrammed_texts[:3]]
>> [['новостройка',
  'нижегородский_область', # нграм
  'новостро́йка',
  '—',
  'сельский',
  'посёлок',
  'в',
  'дивеевский_район', # нграм
  'нижегородский_область', #нграмм
  'входить',
  'в',
  'состав_сатисский', #нграмм
  'сельсовет',
  'посёлок',
  'расположить',
  'в',
  '12,5',
  'километр',
....

Если вы не видите нграммов, то попробуйте изменить параметр threshold

Tfidf добавляется вот так (после векторизации и перед обучением lda)

In [ ]:
tfidf = gensim.models.TfidfModel(corpus, id2word=dictionary, )
corpus = tfidf[corpus]

### Данные

In [130]:
wiki_texts = open('data/wiki_data.txt', encoding='utf-8').read().splitlines()

In [125]:
import re

In [132]:
clean_texts = []
for wtext in wiki_texts[:7000]:
    clean_texts.append(re.sub('#+', ' ',wtext))

In [150]:
texts = [strip_punct(lemmatization(text.split())) for text in clean_texts]

### 1. Gensim LDA

In [193]:
dictionary = gensim.corpora.Dictionary((text.split() for text in texts))

In [194]:
dictionary.filter_extremes(no_above=0.2, no_below=10)
dictionary.compactify()

In [195]:
corpus = [dictionary.doc2bow(text.split()) for text in texts]

In [196]:
lda = gensim.models.LdaModel(corpus, 100, id2word=dictionary, passes=5)

In [197]:
lda.print_topics()

[(7,
  '0.048*"рак" + 0.042*"open" + 0.033*"философия" + 0.029*"елена" + 0.029*"павел" + 0.027*"de" + 0.026*"михаил" + 0.023*"уэльс" + 0.021*"la" + 0.019*"ольга"'),
 (90,
  '0.014*"государственный" + 0.012*"организация" + 0.010*"право" + 0.010*"президент" + 0.010*"председатель" + 0.009*"закон" + 0.008*"дело" + 0.008*"министр" + 0.008*"комитет" + 0.008*"политический"'),
 (17,
  '0.020*"состав" + 0.013*"указ" + 0.012*"станица" + 0.011*"реформа" + 0.011*"российский" + 0.010*"постановление" + 0.010*"век" + 0.009*"город" + 0.008*"территория" + 0.008*"согласно"'),
 (29,
  '0.047*"фамилия" + 0.036*"хан" + 0.029*"лука" + 0.028*"известный" + 0.027*"корпус" + 0.025*"надпись" + 0.022*"клетка" + 0.019*"сторона" + 0.018*"1941" + 0.018*"феликс"'),
 (14,
  '0.278*"доктор" + 0.144*"эпизод" + 0.059*"патрик" + 0.044*"fox" + 0.043*"франсуа" + 0.036*"джонс" + 0.035*"одиннадцать" + 0.027*"«доктор" + 0.023*"серия" + 0.020*"телесериал"'),
 (43,
  '0.026*"польский" + 0.019*"польша" + 0.019*"оркестр" + 0.014*"

In [198]:
pyLDAvis.enable_notebook()

In [199]:
# На графике должно быть как можно меньше пересекающихся кружков (т.е. темы состоят из разных слов),
# а сами кружки не должны быть огромными (скорее всего такую тему можно разбить на несколько поменьше).

pyLDAvis.gensim_models.prepare(lda, corpus, dictionary)

PreparedData(topic_coordinates=              x         y  topics  cluster      Freq
topic                                               
59     0.165241 -0.168629       1        1  6.926637
81     0.199909 -0.119363       2        1  4.285410
74     0.122530  0.102086       3        1  4.012503
89     0.137967 -0.225392       4        1  4.006088
95     0.141552 -0.172851       5        1  3.841289
25     0.171605  0.087622       6        1  2.947655
33     0.067828  0.228404       7        1  2.837703
91     0.184880 -0.020852       8        1  2.757901
31     0.138486  0.102161       9        1  2.721010
21     0.164314 -0.132911      10        1  2.541111
90     0.142326  0.119004      11        1  2.500806
75     0.171131 -0.170298      12        1  2.481627
48     0.184269  0.074481      13        1  2.364907
8      0.137472  0.017579      14        1  1.905767
72     0.162974 -0.053527      15        1  1.854086
49     0.184757 -0.043436      16        1  1.800560
40     0.114466 -0.013616      17        1  1.655747
57     0.130709  0.129359      18        1  1.640007
84    -0.031573  0.053554      19        1  1.608633
38     0.095206  0.048223      20        1  1.466708
86     0.052658  0.073557      21        1  1.465639
80     0.036831  0.242147      22        1  1.432753
88    -0.087450  0.155069      23        1  1.406751
60     0.044426 -0.083296      24        1  1.401122
98     0.152619 -0.109540      25        1  1.383775
32     0.055165  0.103761      26        1  1.332643
78    -0.028358  0.142880      27        1  1.214390
37     0.117071 -0.155803      28        1  1.158111
3      0.127894  0.003409      29        1  1.150335
17     0.078711  0.160662      30        1  1.122047
...         ...       ...     ...      ...       ...
10    -0.113492  0.001560      71        1  0.303974
29    -0.059982 -0.000054      72        1  0.262596
85    -0.078893  0.033409      73        1  0.243549
34    -0.056220  0.014818      74        1  0.243241
47    -0.112523 -0.028412      75        1  0.231471
20    -0.077039  0.018469      76        1  0.228891
30    -0.085789 -0.041406      77        1  0.210545
62    -0.119410  0.020923      78        1  0.202881
68    -0.099443 -0.042213      79        1  0.194951
42    -0.065260 -0.062692      80        1  0.191518
1     -0.129561 -0.041560      81        1  0.191317
65    -0.107940 -0.041168      82        1  0.187435
7     -0.124211  0.002575      83        1  0.182107
26    -0.108430  0.023923      84        1  0.171483
92    -0.113497 -0.079782      85        1  0.167648
4     -0.156530 -0.035809      86        1  0.154647
54    -0.178865 -0.037404      87        1  0.153384
16    -0.135733 -0.033483      88        1  0.136903
73    -0.141422 -0.023382      89        1  0.135206
15    -0.140377 -0.071784      90        1  0.134508
64    -0.159988 -0.007997      91        1  0.132337
67    -0.166917  0.007182      92        1  0.129160
63    -0.161662 -0.036117      93        1  0.124491
52    -0.171829 -0.022713      94        1  0.122126
14    -0.184752 -0.057013      95        1  0.096574
9     -0.185184 -0.054968      96        1  0.095134
39    -0.180822 -0.059166      97        1  0.086148
45    -0.168954 -0.041175      98        1  0.085575
82    -0.188069 -0.063244      99        1  0.071866
2     -0.188587 -0.048981     100        1  0.070053

[100 rows x 5 columns], topic_info=                Term         Freq        Total  Category  logprob  loglift
281             игра  2684.000000  2684.000000   Default  30.0000  30.0000
2677     олимпийский  1910.000000  1910.000000   Default  29.0000  29.0000
28             город  3271.000000  3271.000000   Default  28.0000  28.0000
56          название  1499.000000  1499.000000   Default  27.0000  27.0000
94            состав  2740.000000  2740.000000   Default  26.0000  26.0000
1616            клуб  1207.000000  1207.000000   Default  25.0000  25.0000
160              или  2594.000000  2594.000000   Default  24.0000  24

In [200]:
# Перплексия показывает насколько хороше моделируется корпус. 
# Чем ближе к нулю, тем лучше. 
# Можно использовать, чтобы настраивать количество
# проходов по корпусу (когда перестало улучшаться, то можно останавливаться).

np.exp2(-lda.log_perplexity(corpus))

339.43026554999835

In [201]:
# Ещё есть когерентность.
# Она численно оценивает качество тем
# (проверяется, что темы состоят из разных слов и что в теме есть топ тематических слов).
# Чем выше, тем лучше.

topics = []
for topic_id, topic in lda.show_topics(num_topics=100, formatted=False):
    topic = [word for word, _ in topic]
    topics.append(topic)

In [202]:
coherence_model_lda = gensim.models.CoherenceModel(topics=topics, 
                                                   texts=[text.split() for text in texts], 
                                                   dictionary=dictionary, coherence='c_v')

In [203]:
coherence_model_lda.get_coherence()

0.5377789535926254

### 2. Gensim LDA + n-gramms

In [204]:
corpus2 = [text.split() for text in texts]
ph = gensim.models.Phrases(corpus2, scoring='npmi', threshold=0.5) # threshold можно подбирать
p = gensim.models.phrases.Phraser(ph)
texts_ngramms = p[corpus2]

In [205]:
dictionary_ngramms = gensim.corpora.Dictionary((text for text in texts_ngramms))

In [206]:
dictionary_ngramms.filter_extremes(no_above=0.2, no_below=10)
dictionary_ngramms.compactify()

In [207]:
corpus_ngramms = [dictionary_ngramms.doc2bow(text) for text in texts_ngramms]

In [208]:
lda_ngramms = gensim.models.LdaModel(corpus_ngramms, 100, id2word=dictionary_ngramms, passes=5)

In [209]:
lda_ngramms.print_topics()

[(92,
  '0.046*"сезон" + 0.029*"команда" + 0.026*"гонка" + 0.018*"этап" + 0.014*"чемпионат_мир" + 0.013*"lotus" + 0.012*"гран-при" + 0.012*"три" + 0.012*"нидерландов" + 0.012*"место"'),
 (33,
  '0.115*"шведский" + 0.079*"латвия" + 0.060*"ян" + 0.058*"литовский" + 0.037*"чешский" + 0.027*"рига" + 0.024*"туркестанский" + 0.023*"рижский" + 0.020*"великое_княжество" + 0.018*"король"'),
 (44,
  '0.022*"программа" + 0.021*"сеть" + 0.020*"система" + 0.016*"канал" + 0.013*"использовать" + 0.011*"проект" + 0.010*"оператор" + 0.010*"помощь" + 0.010*"протокол" + 0.008*"позволять"'),
 (45,
  '0.026*"высота" + 0.023*"м" + 0.014*"или" + 0.012*"°c" + 0.012*"длина" + 0.012*"часть" + 0.011*"вод" + 0.011*"температура" + 0.009*"достигать" + 0.008*"около"'),
 (74,
  '0.085*"собака" + 0.052*"порода" + 0.036*"употребление" + 0.032*"собак" + 0.026*"хвост" + 0.023*"луи" + 0.020*"мексика" + 0.018*"животных" + 0.016*"пищевой" + 0.015*"лесна"'),
 (71,
  '0.097*"звезда" + 0.081*"украине_находиться" + 0.069*"челов

In [210]:
pyLDAvis.gensim_models.prepare(lda_ngramms, corpus_ngramms, dictionary_ngramms)

PreparedData(topic_coordinates=              x         y  topics  cluster      Freq
topic                                               
27    -0.178098  0.133219       1        1  6.300015
37    -0.189889  0.134070       2        1  6.087091
68    -0.135458  0.257499       3        1  5.379624
75    -0.166791  0.124716       4        1  3.932210
98    -0.116824 -0.216049       5        1  3.315204
96    -0.174193  0.027741       6        1  3.191626
78    -0.179807 -0.062064       7        1  2.911728
85    -0.209000 -0.090804       8        1  2.680131
91    -0.184309 -0.172582       9        1  2.458706
79    -0.126867 -0.082748      10        1  2.338419
25    -0.116568  0.152672      11        1  2.148153
90    -0.105049 -0.190990      12        1  2.139296
61    -0.182750  0.004277      13        1  1.830426
56    -0.117078  0.144049      14        1  1.808870
13    -0.177836  0.054033      15        1  1.705460
16    -0.124609 -0.066269      16        1  1.613378
15    -0.091750 -0.049166      17        1  1.604345
99    -0.076120  0.198281      18        1  1.593578
2     -0.116261  0.129665      19        1  1.584090
36    -0.117372  0.048359      20        1  1.476502
73    -0.164364 -0.054081      21        1  1.459476
57    -0.106575  0.049152      22        1  1.387857
55    -0.099581  0.091620      23        1  1.384400
4     -0.051773 -0.085285      24        1  1.349192
9     -0.122591  0.033478      25        1  1.286223
46    -0.059186 -0.180238      26        1  1.250786
42    -0.029626  0.096354      27        1  1.221341
38     0.027428 -0.117283      28        1  1.200842
76    -0.108116  0.017079      29        1  1.163871
80     0.039713 -0.031020      30        1  1.144565
...         ...       ...     ...      ...       ...
86     0.080627  0.085981      71        1  0.305858
8      0.051943  0.029182      72        1  0.302963
10     0.075681  0.097678      73        1  0.291464
70     0.054951  0.003120      74        1  0.271500
23     0.081529  0.103236      75        1  0.268462
95     0.046599 -0.055043      76        1  0.267402
69     0.117081 -0.108188      77        1  0.260091
14     0.103368 -0.072232      78        1  0.256958
65     0.103738 -0.061281      79        1  0.247362
53     0.070780 -0.054750      80        1  0.228715
74     0.101014  0.017722      81        1  0.220226
97     0.104977  0.024979      82        1  0.216787
43     0.054422 -0.044698      83        1  0.209550
26     0.115615  0.023763      84        1  0.191325
40     0.125690  0.033697      85        1  0.186794
5      0.121055  0.060256      86        1  0.176514
20     0.155718  0.023572      87        1  0.168700
84     0.123657 -0.030921      88        1  0.151214
88     0.158204  0.022652      89        1  0.145786
58     0.160978 -0.006473      90        1  0.144887
33     0.155049  0.007054      91        1  0.140060
59     0.130533  0.041005      92        1  0.130874
51     0.156444  0.030657      93        1  0.126792
41     0.182563 -0.016765      94        1  0.122063
29     0.154845 -0.010047      95        1  0.117703
71     0.186800 -0.012552      96        1  0.115114
30     0.174382  0.028352      97        1  0.092184
93     0.161242 -0.020609      98        1  0.087623
39     0.191842  0.007651      99        1  0.075550
87     0.180734  0.020876     100        1  0.065140

[100 rows x 5 columns], topic_info=                     Term         Freq        Total  Category  logprob  \
27                  город  3205.000000  3205.000000   Default  30.0000   
266                  игра  2027.000000  2027.000000   Default  29.0000   
123                остров  1084.000000  1084.000000   Default  28.0000   
112                 фильм   996.000000   996.000000   Default  27.0000   
566                состав  2568.000000  2568.000000   Default  26.0000   
590                 сесть  1228.000000  1228.000000   Default  25.0000   
754                  уезд   957.000000   957.000000   Default  24.0000   
54

In [211]:
np.exp2(-lda_ngramms.log_perplexity(corpus_ngramms))

411.8113940886415

In [212]:
topics_ngramms = []
for topic_id, topic in lda_ngramms.show_topics(num_topics=100, formatted=False):
    topic = [word for word, _ in topic]
    topics_ngramms.append(topic)

In [217]:
coherence_model_lda_ngramms = gensim.models.CoherenceModel(topics=topics_ngramms, 
                                                   texts=[text for text in texts_ngramms], 
                                                   dictionary=dictionary_ngramms, coherence='c_v')

In [245]:
coherence_model_lda_ngramms.get_coherence()

0.5471739854759489

### 3. Gensim LDA + TF-IDF

In [219]:
dictionary_tf_idf = gensim.corpora.Dictionary((text.split() for text in texts))

In [220]:
dictionary_tf_idf.filter_extremes(no_above=0.2, no_below=10)
dictionary_tf_idf.compactify()

In [221]:
corpus_tf_idf = [dictionary_tf_idf.doc2bow(text.split()) for text in texts]

In [222]:
tfidf = gensim.models.TfidfModel(corpus, id2word=dictionary_tf_idf,)
corpus_tf_idf = tfidf[corpus_tf_idf]

In [223]:
lda_tf_idf = gensim.models.LdaModel(corpus_tf_idf, 100, id2word=dictionary_tf_idf, passes=5)

In [224]:
lda_tf_idf.print_topics()

[(94,
  '0.051*"черниговский" + 0.026*"события" + 0.003*"гонщик" + 0.000*"500" + 0.000*"выиграть" + 0.000*"поэт" + 0.000*"гонка" + 0.000*"стих" + 0.000*"стихи" + 0.000*"сезон"'),
 (18,
  '0.009*"клиент" + 0.005*"волокно" + 0.005*"пакет" + 0.000*"стороне" + 0.000*"услуга" + 0.000*"функция" + 0.000*"удерживать" + 0.000*"нервный" + 0.000*"палец" + 0.000*"плечо"'),
 (33,
  '0.036*"ленина" + 0.020*"«герой" + 0.014*"явление" + 0.012*"обл" + 0.009*"приватизация" + 0.007*"волынский" + 0.007*"380" + 0.006*"чарли" + 0.003*"кабинет" + 0.003*"утвердить"'),
 (76,
  '0.057*"перу" + 0.032*"смит" + 0.029*"ассоциация" + 0.011*"латиноамериканский" + 0.009*"специфический" + 0.006*"миллер" + 0.006*"176" + 0.006*"глобальный" + 0.005*"регулировать" + 0.003*"лихорадка"'),
 (26,
  '0.025*"to" + 0.023*"and" + 0.020*"джордж" + 0.017*"джейн" + 0.015*"rock" + 0.014*"дэйв" + 0.011*"for" + 0.011*"коста-рика" + 0.010*"in" + 0.009*"мая"'),
 (81,
  '0.062*"населить" + 0.062*"пункт" + 0.051*"аэропорт" + 0.015*"порт" + 

In [225]:
pyLDAvis.gensim_models.prepare(lda_tf_idf, corpus_tf_idf, dictionary_tf_idf)

PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
38     0.294955 -0.128436       1        1  11.559811
84     0.295945 -0.135071       2        1   9.834203
59     0.304693 -0.079706       3        1   7.551539
56     0.257849 -0.132445       4        1   5.909025
0      0.286944 -0.115771       5        1   4.777736
49     0.246279 -0.103170       6        1   4.229220
93     0.283986  0.221329       7        1   3.875816
89     0.200565 -0.110252       8        1   3.506718
28     0.187388  0.031082       9        1   3.241563
9      0.213196 -0.036793      10        1   3.055316
55     0.217546  0.110327      11        1   2.630502
60     0.199183  0.082673      12        1   2.324722
16     0.169549  0.034244      13        1   2.059635
68     0.111163  0.205460      14        1   1.864736
85     0.143621  0.008750      15        1   1.839595
42     0.129171  0.035915      16        1   1.485301
92     0.111943  0.083957      17        1   1.312551
71     0.161655  0.259933      18        1   1.288664
69     0.030009  0.003699      19        1   1.009247
86     0.048239 -0.025408      20        1   0.913479
54     0.036171 -0.011079      21        1   0.910393
23     0.105443  0.138538      22        1   0.901926
70     0.012494 -0.010270      23        1   0.859307
31     0.030815  0.000490      24        1   0.826824
63     0.014890  0.004498      25        1   0.817296
50     0.001331 -0.011303      26        1   0.738883
6      0.010497 -0.025199      27        1   0.728598
5     -0.000928 -0.007928      28        1   0.653779
47    -0.017467 -0.012383      29        1   0.599203
72    -0.042972  0.013740      30        1   0.567578
...         ...       ...     ...      ...        ...
26    -0.062317 -0.007676      71        1   0.222125
67    -0.063891 -0.004879      72        1   0.222016
62    -0.062360 -0.003324      73        1   0.220566
51    -0.062772 -0.004394      74        1   0.214289
57    -0.061613 -0.001841      75        1   0.214054
98    -0.062382 -0.004080      76        1   0.209650
87    -0.061506 -0.004575      77        1   0.207977
74    -0.062049 -0.004741      78        1   0.207755
39    -0.062818 -0.005442      79        1   0.206945
33    -0.060197 -0.004874      80        1   0.206733
82    -0.063511 -0.002304      81        1   0.204150
76    -0.062469 -0.005819      82        1   0.203734
46    -0.060226 -0.004750      83        1   0.201676
2     -0.059864 -0.002958      84        1   0.200371
21    -0.060675 -0.005186      85        1   0.199630
15    -0.061550 -0.004323      86        1   0.196075
80    -0.060140 -0.004956      87        1   0.192205
95    -0.059101 -0.004554      88        1   0.190695
17    -0.059437 -0.005028      89        1   0.188790
91    -0.060422 -0.004795      90        1   0.187157
45    -0.058579 -0.008287      91        1   0.186522
19    -0.056476 -0.004636      92        1   0.174560
8     -0.057319 -0.004527      93        1   0.174540
94    -0.058383 -0.004541      94        1   0.170598
7     -0.054982 -0.004361      95        1   0.166832
36    -0.054284 -0.004194      96        1   0.164222
41    -0.054691 -0.004289      97        1   0.163775
18    -0.054027 -0.004198      98        1   0.163497
24    -0.054163 -0.004257      99        1   0.163029
97    -0.052483 -0.004183     100        1   0.156149

[100 rows x 5 columns], topic_info=               Term        Freq       Total  Category  logprob  loglift
2677    олимпийский  147.000000  147.000000   Default  30.0000  30.0000
8242    житомирский  115.000000  115.000000   Default  29.0000  29.0000
281            игра  141.000000  141.000000   Default  28.0000  28.0000
1493            код   67.000000   67.000000   Default  27.0000  27.0000
3737         летний   96.000000   96.000000   Default  26.0000  26.0000
2756         зимний   60.000000   60.000000   Default  25.0000  25.0000
616           сесть   90.00

In [226]:
np.exp2(-lda_tf_idf.log_perplexity(corpus_tf_idf))

26671278919.764896

In [227]:
topics_tf_idf = []
for topic_id, topic in lda_tf_idf.show_topics(num_topics=100, formatted=False):
    topic = [word for word, _ in topic]
    topics_tf_idf.append(topic)

In [228]:
coherence_model_lda_tf_idf = gensim.models.CoherenceModel(topics=topics_tf_idf, 
                                                   texts=[text.split() for text in texts], 
                                                   dictionary=dictionary_tf_idf, coherence='c_v')

In [229]:
coherence_model_lda_tf_idf.get_coherence()

0.44583359752485097

### 4. Gensim LDA + n-gramms + TF-IDF

In [230]:
dictionary_ngramms_tf_idf = gensim.corpora.Dictionary((text for text in texts_ngramms))

In [231]:
dictionary_ngramms_tf_idf.filter_extremes(no_above=0.2, no_below=10)
dictionary_ngramms_tf_idf.compactify()

In [232]:
corpus_ngramms_tf_idf = [dictionary_ngramms_tf_idf.doc2bow(text) for text in texts_ngramms]

In [233]:
tfidf = gensim.models.TfidfModel(corpus_ngramms_tf_idf, id2word=dictionary_ngramms_tf_idf,)
corpus_ngramms_tf_idf = tfidf[corpus_ngramms_tf_idf]

In [234]:
lda_ngramms_tf_idf = gensim.models.LdaModel(corpus_ngramms_tf_idf, 100, id2word=dictionary_ngramms_tf_idf, passes=5)

In [235]:
lda_ngramms_tf_idf.print_topics()

[(25,
  '0.046*"флаг" + 0.034*"символ" + 0.031*"вид_спорта" + 0.024*"зелёный" + 0.020*"австралийский" + 0.019*"австралия" + 0.012*"австралии" + 0.006*"яхта" + 0.000*"суд" + 0.000*"доктор"'),
 (70,
  '0.042*"уезд" + 0.040*"волость" + 0.027*"район" + 0.026*"состав" + 0.017*"сельсовет" + 0.014*"центр" + 0.013*"епархия" + 0.013*"образовать" + 0.013*"административно-территориальный_единица" + 0.012*"территория"'),
 (21,
  '0.099*"фамилия" + 0.021*"анатолий" + 0.019*"месторождение" + 0.018*"литва" + 0.017*"российский_федерация" + 0.016*"партийный" + 0.014*"рсфср" + 0.014*"федерация" + 0.014*"лауреат" + 0.014*"оао"'),
 (33,
  '0.006*"пучок" + 0.004*"электроника" + 0.000*"электронный" + 0.000*"мощность" + 0.000*"физика" + 0.000*"мощный" + 0.000*"соединение" + 0.000*"дивизия" + 0.000*"генерал-лейтенант" + 0.000*"генерал-майор"'),
 (94,
  '0.035*"консерватория" + 0.022*"клетка" + 0.019*"риме" + 0.018*"жидкость" + 0.016*"подача" + 0.012*"фортепианный" + 0.010*"1870" + 0.009*"мёртвый" + 0.008*"фор

In [237]:
pyLDAvis.gensim_models.prepare(lda_ngramms_tf_idf, corpus_ngramms_tf_idf, dictionary_ngramms_tf_idf)

PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
44    -0.316406  0.203998       1        1  13.371182
66    -0.278607  0.226953       2        1   8.938521
12    -0.334317  0.024300       3        1   8.302251
99    -0.263344  0.197115       4        1   7.511825
55    -0.256615 -0.102534       5        1   4.783230
73    -0.261810 -0.052923       6        1   4.523806
49    -0.250781  0.016141       7        1   3.989955
14    -0.260971 -0.150106       8        1   3.226737
86    -0.138342 -0.047898       9        1   2.216842
81    -0.176390 -0.114578      10        1   2.059110
4     -0.199380 -0.124492      11        1   2.046621
22    -0.164788 -0.111316      12        1   1.891749
45    -0.154212  0.050123      13        1   1.724199
30    -0.175551 -0.130310      14        1   1.611300
2     -0.127314  0.071368      15        1   1.602310
70    -0.122982 -0.077477      16        1   1.414169
98    -0.013618 -0.065269      17        1   1.159343
31    -0.060287 -0.030485      18        1   1.142155
34    -0.044761 -0.017220      19        1   0.937712
36     0.007297 -0.008731      20        1   0.936654
11    -0.028628  0.003508      21        1   0.862613
26    -0.025441 -0.007704      22        1   0.847867
93    -0.032654 -0.060368      23        1   0.828300
1      0.003116 -0.022496      24        1   0.746570
65     0.003401 -0.031802      25        1   0.729254
52     0.007454 -0.004340      26        1   0.719850
88    -0.007193 -0.019117      27        1   0.706938
21    -0.001365 -0.022965      28        1   0.634383
13    -0.004431  0.012274      29        1   0.609929
87     0.027238  0.003258      30        1   0.594375
...         ...       ...     ...      ...        ...
76     0.055836  0.006197      71        1   0.227653
7      0.057545  0.007179      72        1   0.226470
29     0.056147  0.004413      73        1   0.225892
58     0.056601  0.005538      74        1   0.223135
46     0.057699  0.007041      75        1   0.221235
67     0.056106  0.005614      76        1   0.220105
63     0.055202  0.008291      77        1   0.216577
68     0.056247  0.006387      78        1   0.214229
37     0.055772  0.007394      79        1   0.209329
5      0.055020  0.006108      80        1   0.208836
89     0.054371  0.003273      81        1   0.208035
3      0.055808  0.007162      82        1   0.207172
35     0.056831  0.007137      83        1   0.206996
62     0.055581  0.006404      84        1   0.205166
72     0.055074  0.006026      85        1   0.204343
6      0.057740  0.006554      86        1   0.203769
92     0.054916  0.005567      87        1   0.203379
97     0.054956  0.006099      88        1   0.197686
64     0.054741  0.006295      89        1   0.195318
91     0.054435  0.005778      90        1   0.194259
80     0.051958  0.006041      91        1   0.187820
75     0.052146  0.005456      92        1   0.184806
32     0.052361  0.006004      93        1   0.182825
17     0.051066  0.005798      94        1   0.177253
8      0.050036  0.005833      95        1   0.171855
59     0.049456  0.005714      96        1   0.171484
48     0.049135  0.005713      97        1   0.168984
0      0.048164  0.005448      98        1   0.168043
33     0.047591  0.005501      99        1   0.165115
71     0.047121  0.005420     100        1   0.162727

[100 rows x 5 columns], topic_info=                         Term        Freq       Total  Category  logprob  \
590                     сесть  100.000000  100.000000   Default  30.0000   
11203     житомирский_область   76.000000   76.000000   Default  29.0000   
3755       летний_олимпийский  108.000000  108.000000   Default  28.0000   
266                      игра  121.000000  121.000000   Default  27.0000   
5111                    хутор   72.000000   72.000000   Default  26.0000   
54                  население   76.000000   76.000000   Default  25.0000   

In [240]:
np.exp2(-lda_ngramms_tf_idf.log_perplexity(corpus_ngramms_tf_idf))

120230087240.71335

In [242]:
topics_ngramms_tf_idf = []
for topic_id, topic in lda_ngramms_tf_idf.show_topics(num_topics=100, formatted=False):
    topic = [word for word, _ in topic]
    topics_ngramms_tf_idf.append(topic)

In [243]:
coherence_model_lda_ngramms_tf_idf = gensim.models.CoherenceModel(topics=topics_ngramms_tf_idf, 
                                                   texts=[text for text in texts_ngramms], 
                                                   dictionary=dictionary_ngramms_tf_idf, coherence='c_v')

In [244]:
coherence_model_lda_ngramms_tf_idf.get_coherence()

0.4255875221760534

Выводы:

По темам мне показались наиболее осмысленными результаты простой модели LDA и LDA c n-граммами.

По перплексии лучше всего показала себя простая модель LDA (339.43..); хуже всех - LDA c n-граммами и TF-IDF (120230087240.713..);

По когерентности лучше всего показала себя модель LDA c n-граммами и TF-IDF (0.425..); хуже всех - LDA c n-граммами (0.547..).